In [1]:
%load_ext autoreload
%autoreload 2

import pathlib
from datetime import timedelta

import pandas as pd
pd.set_option('display.max_rows', 200)
import plotly.express as px

from tqdm import tqdm

from data_handlers.runtimes import *

In [2]:
experiment_path = pathlib.Path(f"/home/sterz/maci-docker-compose/maci_data/binary_files")
experiment_ids = ["dtn7ng_mobile", "dtn7rs_mobile", "ibrdtn_mobile", "serval_mobile"]

In [3]:
orig_event_frame = parse_bundle_events(experiment_path, experiment_ids, True)

Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6548


Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6535
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6542
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6499
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6477
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6507
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6493
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6526
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6551
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6514
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6480
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6464
Parsing /home/sterz/maci-docker-compose/maci_data/binary_files/dtn7ng_mobile/6487
Parsing /home/st

In [4]:
event_frame = orig_event_frame.copy()

In [5]:
event_frame = event_frame[event_frame["# Payloads"] != 10]

event_frame = event_frame.replace("IBRDTN", "IBR-DTN")
event_frame = event_frame.replace("DTN7NG", "DTN7-go")
event_frame = event_frame.replace("DTN7Rs", "DTN7-rs")


event_frame = event_frame.replace("mtcp", "MTCP")
event_frame = event_frame.replace("http", "HTTP")
event_frame = event_frame.replace("tcp", "TCPCL")
event_frame = event_frame.replace("quicl", "QUICL")

event_frame = event_frame.rename(columns={"Payload Size": "Bundle Size"})
event_frame = event_frame.rename(columns={"# Payloads": "# Bundles"})

event_frame["Software/CLP"] = event_frame['Software'] + "/" + event_frame['CLA']

event_frame = event_frame.replace("Serval/default", "Serval")

event_frame["Bundle Size"] = event_frame["Bundle Size"].replace(1000, "1 kB")
event_frame["Bundle Size"] = event_frame["Bundle Size"].replace(100000, "100 kB")
event_frame["Bundle Size"] = event_frame["Bundle Size"].replace(1000000, "1 MB")

In [6]:
creation_instances = event_frame[event_frame.Event == "creation"].groupby("Simulation ID")
delivery_instances = event_frame[event_frame.Event == "delivery"]

In [7]:
delivered_list = []
runtime_list = []
for sim_instance_id, creations in tqdm(creation_instances):
    deliveries_sid = delivery_instances[delivery_instances["Simulation ID"] == sim_instance_id]
    
    for _, row in creations.iterrows():
        # Compute deliverys
        bundle = row.Bundle
        deliveries = deliveries_sid[deliveries_sid.Bundle == bundle]

        was_delivered = not deliveries.empty

        row_dict = {
            "Simulation ID": sim_instance_id,
            "Bundle": bundle,
            "Delivered": was_delivered,
            "CLA": row.CLA,
            "Software/CLP": row["Software/CLP"],
            "Movement": row.movement,
            "Bundle Size": row["Bundle Size"],
            "Software": row.Software,
            "# Bundles": row["# Bundles"],
        }
        delivered_list.append(row_dict)        
        
        # Compute runtimes
        if was_delivered:
            delivery_time = deliveries["Timestamp"].min()
            creation_time = row["Timestamp"]
            runtime = delivery_time - creation_time
            
            runtime_dict = {
                "Simulation ID": sim_instance_id,
                "Bundle": bundle,
                "Runtime": (runtime.to_pytimedelta() / timedelta(milliseconds=1)) / 1000,
                "CLA": row.CLA,
                "Software/CLP": row["Software/CLP"],
                "Movement": row.movement,
                "Software": row.Software,
                "Bundle Size": row["Bundle Size"],
                "# Bundles": row["# Bundles"],
            }
            runtime_list.append(runtime_dict)
        
delivered_df = pd.DataFrame(delivered_list)
runtime_df = pd.DataFrame(runtime_list)

  0%|          | 0/210 [00:00<?, ?it/s]

100%|██████████| 210/210 [03:55<00:00,  1.12s/it]


In [8]:
row_dicts = []

for sim_instance_id, bundles in delivered_df.groupby("Simulation ID"):
    cla = bundles["CLA"].values[0]
    software_clp = bundles["Software/CLP"].values[0]
    movement = bundles["Movement"].values[0]
    software = bundles["Software"].values[0]
    payload_size = bundles["Bundle Size"].values[0]
    payloads = bundles["# Bundles"].values[0]
    
    total_bundles =  payloads
    delivered_bundles = len(bundles[bundles.Delivered == True].index)
    
    row_dict = {
        "Simulation ID": sim_instance_id,
        "Delivered (%)": (float(delivered_bundles) / float(total_bundles)) * 100,
        "CLA": cla,
        "Software/CLP": software_clp,
        "Movement": movement,
        "Software": software,
        "Bundle Size": payload_size,
        "# Bundles": payloads,
    }
    
    row_dicts.append(row_dict)

ratio_df = pd.DataFrame.from_dict(row_dicts)

In [9]:
fig = px.box(
    runtime_df,
    x="Software/CLP", 
    y="Runtime",
    color="Bundle Size",
    facet_col="# Bundles",
    labels={
        "Runtime": "Runtime (s)",
        "# Bundles": "Bundles"
    },
    category_orders={
        "Bundle Size": ["1 kB", "100 kB", "1 MB"],
        "Software/CLP": ["Serval", "IBR-DTN/TCPCL", "DTN7-rs/MTCP", "DTN7-rs/TCPCL", "DTN7-rs/HTTP", "DTN7-go/MTCP", "DTN7-go/QUICL"],
        "# Bundles": [100, 1000]
    },
)

fig.for_each_annotation(lambda a: a.update(text=a.text.replace("=", ": ")))
fig.for_each_annotation(lambda a: a.update(text=a.text.replace("Bundle Size: ", "")))

fig.for_each_yaxis(lambda y: y.update(title = ''))
fig.add_annotation(
    x=-0.06, y=0.3,
    text="Runtime (s)",
    textangle=-90,
    xref="paper", yref="paper"
)

fig.update_layout(
    font=dict(
        size=16,
    )
)
fig.update_xaxes(tickangle=45)

fig.write_image("runtime_mobile.pdf", width=1000, height=375)
fig

In [10]:
fig = px.box(
    ratio_df,
    x="Software/CLP", 
    y="Delivered (%)",
    color="Bundle Size",
    facet_col="# Bundles",
    labels={
        "Runtime": "Runtime (s)",
        "# Bundles": "Bundles",
        "Delivered (%)": "Successful Receptions (%)"
    },
    category_orders={
        "Bundle Size": ["1 kB", "100 kB", "1 MB"],
        "Software/CLP": ["Serval", "IBR-DTN/TCPCL", "DTN7-rs/MTCP", "DTN7-rs/TCPCL", "DTN7-rs/HTTP", "DTN7-go/MTCP", "DTN7-go/QUICL"],
        "# Bundles": [100, 1000]
    },
)

fig.for_each_annotation(lambda a: a.update(text=a.text.replace("=", ": ")))
fig.for_each_annotation(lambda a: a.update(text=a.text.replace("Bundle Size: ", "")))

fig.for_each_yaxis(lambda y: y.update(title = ''))
fig.add_annotation(
    x=-0.06, y=0.3,
    text="Successful Receptions (%)",
    textangle=-90,
    xref="paper", yref="paper"
)

fig.update_layout(
    font=dict(
        size=16,
    )
)
fig.update_xaxes(tickangle=45)

fig.write_image("delivered_mobile.pdf", width=1000, height=375)
fig